In [5]:
# DATA LOADING

from utils.data_loader.mobility_data_loader import mobility_data_loader 

# Process whole dataset in to intermediate form
dataframe = mobility_data_loader('20240101','20240107')

1
20240101 dataframe shape
(85653, 18)
2
20240102 dataframe shape
(84857, 18)
3
20240103 dataframe shape
(85335, 18)
4
20240104 dataframe shape
(101273, 18)
5
20240105 dataframe shape
(113529, 18)
6
20240106 dataframe shape
(104928, 18)
7
20240107 dataframe shape
(94203, 18)


In [6]:
# Get parent map
from utils.folium_mapper.ishikawa_region_mapper import ishikawa_region_mapper
map, jpn_adm2 = ishikawa_region_mapper()

# Plot shelter
from utils.plotter.shelter_plotter import shelter_plotter
map = shelter_plotter(map)


Former Wajima City Nishiho Elementary School (gymnasium) [37.38261579565501, 136.81424758734263]
Wajima City Kugenosu Community Center [37.3887805593711, 136.9058392770779]
Hotel Route Inn Wajima [37.39597809456971, 136.90518517876185]
Nursing care prevention center facility Fureai Plaza Nisei [37.38663604924676, 136.89569480420437]
Wajima City Oya Community Center [37.38114152151224, 136.88597975188142]
Wajima City Mitsui Community Center [37.31533624424696, 136.90266106890422]
Wajima City Minamishimi Community Center [37.43005269744418, 137.03405593697457]
Wajima City Machino Community Center [37.42333586505611, 137.08810393299623]
Wajima City Kawarada Community Center [37.357284054003365, 136.9083157628509]
Wajima City Urakami Community Center [37.30572509864802, 136.79769779960344]
Wajima City Hongo Community Center [37.284818934685525, 136.826961147374]
Tsurugi Nuclear Disaster Protection Facility [37.231530829269374, 136.71024546346436]
Wajima City Agishi Community Center [37.231

In [7]:
import pandas as pd
from utils.resident.resident_classification import resident_classification
from utils.plotter.evacuation_plotter import evacuation_plotter

for day, df in dataframe.items():    
    df_residents = resident_classification(df)

    if day == '20240101':
        earthquake_time = pd.to_datetime('2024-01-01 16:10:00')
        df_residents = df_residents[df_residents['depart_time_o'] > earthquake_time]
        map = evacuation_plotter(map, df_residents)
    else:
        map = evacuation_plotter(map, df_residents)

C:\Users\HP\AppData\Local\Temp\ipykernel_18588\1445390916.py:6: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  df_residents = resident_classification(df)
C:\Users\HP\AppData\Local\Temp\ipykernel_18588\1445390916.py:6: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  df_residents = resident_classification(df)
C:\Users\HP\AppData\Local\Temp\ipykernel_18588\1445390916.py:6: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  df_residents = resident_classification(df)
C:\Users\HP\AppData\Local\Temp\ipykernel_18588\1445390916.py:6: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  df_residents = resident_classification(df)
C:\Users\HP\AppData\Loca

In [8]:
map 

In [10]:
for day, df in dataframe.items():
    print(day,df.shape)

20240101 (85653, 25)
20240102 (84857, 25)
20240103 (85335, 25)
20240104 (101273, 25)
20240105 (113529, 25)
20240106 (104928, 25)
20240107 (94203, 25)


In [ ]:
import pandas as pd
from utils.resident.resident_classification import resident_classification

concat_df = pd.DataFrame()

for day, df in dataframe.items():    
    df_residents = resident_classification(df)

    if day == '20240101':
        earthquake_time = pd.to_datetime('2024-01-01 16:10:00')
        df_residents = df_residents[df_residents['depart_time_o'] > earthquake_time]
    
    df_residents = df_residents[df_residents['stay_time_d'] >= 240]
    
    print(df_residents.shape)

    # contcatenate
    concat_df = pd.concat([concat_df,df_residents], ignore_index=True)

print(concat_df.shape)

In [30]:
# Sort the concatenated DataFrame by stay_time_d from big to small
sorted_df = concat_df.sort_values(by='stay_time_d', ascending=True)

# Divide the stay_time_d by 60
sorted_df['stay_time_d'] = sorted_df['stay_time_d'] / 60

sorted_df['stay_time_d'].describe() 

count    2958.000000
mean       21.774256
std        59.973449
min         4.000000
25%         7.887500
50%        13.050000
75%        19.450000
max      1704.733333
Name: stay_time_d, dtype: float64

In [28]:
# Create a list of x-axis labels
x_labels = sorted_df.index.tolist()

In [31]:
import pandas as pd
import plotly.graph_objs as go
import plotly.express as px


# Create a unique identifier for each row for the x-axis
sorted_df['resident_id'] = range(1, len(sorted_df) + 1)

# Generate the plotly graph
fig = go.Figure()

fig.add_trace(go.Bar(
    x=sorted_df['resident_id'],  # Use the resident_id for the x-axis
    y=sorted_df['stay_time_d'],
    marker=dict(color='purple')
))

# Update layout
fig.update_layout(
    title='Stay Time Duration of Residents (in hours)',
    xaxis=dict(
        title='Residents',
        showticklabels=False  # Hide the x-axis ticks
    ),
    yaxis=dict(
        title='Stay Time Duration (hours)'
    )
)

# Show the figure
fig.show()